The analysis in  Fig. 1 of Kornhuber et al. 2024 (PNAS) proceeds from tasmax (daily-max. temperature at 2 meters) from ERA5 covering the period 1950–2023. This code produces all panels in Fig. 2–4 if appropriate data is given.

# Imports etc.

In [17]:
import dask
from dask.distributed import Client, LocalCluster
import numpy as np
import xarray as xr
import matplotlib.pyplot as plt
from matplotlib.lines import Line2D
import matplotlib.gridspec as gridspec
import matplotlib_inline
%config InlineBackend.figure_format='retina'
import glob
import pathlib
from dask.diagnostics import ProgressBar
pbar = ProgressBar()
import cartopy
import cartopy.crs as ccrs
import cartopy.feature as cfeature
from cartopy.util import add_cyclic_point
import seaborn as sns
import os
import copy
from string import ascii_lowercase
from scipy import stats
tinv = lambda p, df: abs(stats.t.ppf(p/2, df))
from datetime import datetime
import pandas as pd
print(datetime.now())

matplotlib_inline.backend_inline.set_matplotlib_formats('pdf')
plt.rcParams['pdf.fonttype'] = 42
plt.rcParams['hatch.linewidth'] = .25


2024-09-20 11:59:19.075438


# Load data


In [ ]:
# Load tasmax, calculate anomalies and date of all-time maximum
tx = xr.open_mfdataset(glob.glob('/data0/samuelb/era5/t2m/era5_t2m_1dmax_????.nc')).t2m
tx = tx.assign_coords(longitude = (tx.coords['longitude'] + 180) % 360 - 180).sortby('longitude')
tx_anom_plotting = (tx.sel(time=slice('2016','2024')).groupby('time.dayofyear') - tx.sel(time=slice('1981','2010')).groupby('time.dayofyear').mean()).compute()
tx_idxmaxtime = tx.idxmax('time').compute()


In [6]:
# Load land-sea mask
lsm = xr.open_dataarray('/data0/samuelb/era5_lsm.nc').squeeze()
lsm = lsm.assign_coords(longitude = (lsm.coords['longitude'] + 180) % 360 - 180).sortby('longitude')
weights = np.cos(np.deg2rad(lsm.latitude)); weights.name = "weights"


In [4]:
# More regions than are ultimately shown in Fig. 1
regions = ['pnw','us','uk','china','russia','amazon','sahel','seasia','rio','sahel_s','sahel_n','s_africa']
regtitles = ['Pacific Northwest','Southern U.S.','Northwest Europe','Central China','Central Russia','Amazon Basin','Western Sahel','Southeast Asia','Rio De Janeiro','Western Sahel','Western Sahel','Southern Africa']
reglats = [[45,59],[27,37],[48,57],[27,37],[52,65],[-10,5],[8,20],[10,25],[-25,-19],[10,16],[13,20],[-33,-19]]
reglons = [[-127,-113],[-107,-97],[-5,5],[95,110],[69,85],[-75,-55],[-12,4],[98,108],[-47,-39],[-12,4],[-12,4],[17,31]]
regranges = [(slice(reglat[0],reglat[1]),slice(reglon[0],reglon[1])) for reglat,reglon in zip(reglats,reglons)]
regmaptimes = [
    slice('June 27, 2021','July 1, 2021'),
    slice('June 25, 2023','June 28, 2023'),
    slice('July 18, 2022','July 19, 2022'),
    slice('June 3, 2023','June 5, 2023'),
    slice('June 4, 2023','June 7, 2023'),
    slice('September 26, 2023','October 8, 2023')
    slice('March 31, 2024','April 4, 2024'),
    slice('April 26, 2024','April 30, 2024'),
    slice('November 13, 2023','November 18, 2023'),
    slice('March 31, 2024','April 4, 2024'),
    slice('March 31, 2024','April 4, 2024'),
    slice('January 2, 2016','January 7, 2016'),
]
# Months between climatological warming/cooling
regseasons = [[6,7,8],[6,7,8],[6,7,8],[6,7,8],[6,7,8],[9,10,11],[3,4,5,6],[3,4,5],[11,12,1,2,3],[3,4,5,6],[3,4,5,6],[12,1,2]]


In [ ]:
# Select regions for Fig. 1
regsels = [0,2,5,11]
reg_tx_abs = []
reg_tx_anoms = []
reg_tx_maxanoms = []
reg_tx_maxanomdates = []
reg_tx_meananoms = []
for regsel in regsels:
    regrange,region,regseason = regranges[regsel],regions[regsel],regseasons[regsel]
    print(f'{region} START:        {datetime.now()}')
    reg_tx_cass = tx_cass.sel(time=tx_cass.time.dt.month.isin(regseason)).sel(latitude=slice(regrange[0].stop,regrange[0].start),longitude=regrange[1]).compute()
    reg_tx_online = tx_online.sel(time=tx_online.time.dt.month.isin(regseason)).sel(latitude=slice(regrange[0].stop,regrange[0].start),longitude=regrange[1]).compute()
    reg_tx = xr.concat([reg_tx_cass,reg_tx_online],'time').where(lsm>0.5).sortby('latitude')
    reg_tx_abs.append(reg_tx)
    reg_tx_anom = reg_tx.groupby('time.dayofyear') - reg_tx.sel(time=slice('1981','2010')).groupby('time.dayofyear').mean()
    reg_tx_anoms.append(reg_tx_anom)
    reg_tx_anom_mean = reg_tx_anom.weighted(weights).mean(('latitude','longitude'))
    reg_tx_maxanom = reg_tx_anom_mean.resample(time=f'{"1Y" if region not in ["s_africa"] else "A-FEB"}').max()
    reg_tx_maxanom = reg_tx_maxanom.assign_coords(year=reg_tx_maxanom.time.dt.year).swap_dims({'time':'year'}).sel(year=slice(f'{"1950" if region not in ["s_africa"] else "1951"}','2024'))
    reg_tx_maxanoms.append(reg_tx_maxanom)
    reg_tx_maxanomdate = reg_tx_maxanom.copy(data=[reg_tx_anom_mean.where(reg_tx_anom_mean==anomval,drop=True).time.values[0] for anomval in reg_tx_maxanom])
    reg_tx_maxanomdates.append(reg_tx_maxanomdate)
    reg_tx_meananom = reg_tx_anom_mean.resample(time=f'{"1Y" if region not in ["s_africa"] else "A-FEB"}').mean()
    reg_tx_meananom = reg_tx_meananom.assign_coords(year=reg_tx_meananom.time.dt.year).swap_dims({'time':'year'}).sel(year=slice(f'{"1950" if region not in ["s_africa"] else "1951"}','2024'))
    reg_tx_meananoms.append(reg_tx_meananom)
    

pnw START:        2024-09-17 16:04:57.897469
uk START:        2024-09-17 16:05:37.084687
amazon START:        2024-09-17 16:06:15.349680
s_africa START:        2024-09-17 16:06:53.934621


# Create figure

In [39]:
zooms = [20,20,10,10]
sizeadjust = .9
widthadjust = .9

fig = plt.figure(figsize=(9*widthadjust*sizeadjust,3*len(regsels)*sizeadjust),layout='constrained',dpi=2400)
gss = fig.add_gridspec(1,2,width_ratios=[4,5])
gs_left = gss[0].subgridspec(len(regsels),1)
gs_right = gss[1].subgridspec(len(regsels),1)

qq = tx_anom_plotting.sel(latitude=slice(90,-60))
panellabels = [letter for letter in ascii_lowercase[::2][:len(regsels)]]
axs_left = []
for gs,regsel,panellabel,zoom in zip(gs_left,regsels,panellabels,zooms):
    reglon = reglons[regsel]; reglat = reglats[regsel]
    projection = ccrs.NearsidePerspective(central_longitude=np.mean(reglon),central_latitude=np.mean(reglat),satellite_height=35785831/zoom,globe=None); projection.threshold = projection.threshold/1000
    ax = fig.add_subplot(gs,projection=projection); axs_left.append(ax)
    time = regmaptimes[regsel]
    ax.stock_img()
    scale = (qq.sel(latitude=slice(reglat[1],reglat[0]),longitude=slice(reglon[0],reglon[1])).sel(time=time).mean('time').where(lsm>0.5).quantile(.9)/2).round()*2; step = np.ceil(scale/10); levels = np.arange(-scale,scale+step,step)
    pcol = qq.sel(time=time).mean('time').where(lsm>0.5).T.plot.pcolormesh(ax=ax,transform=ccrs.PlateCarree(),vmax=scale,vmin=-scale,levels=levels,extend='both',cmap='coolwarm',cbar_kwargs={'shrink':.8,'location':'left','label':'Tx anomaly [°C]'},linewidth=0,rasterized=True); pcol.set_edgecolor('face')#imshow 
    ax.coastlines('50m',color='0',lw=.2); ax.add_feature(cfeature.NaturalEarthFeature('cultural','admin_0_boundary_lines_land','50m',facecolor='none',edgecolor='0',lw=.2)); ax.add_feature(cfeature.NaturalEarthFeature('cultural','admin_1_states_provinces_lines','50m',facecolor='none',edgecolor='.7',lw=.2)); ax.add_feature(cfeature.NaturalEarthFeature('physical','rivers_lake_centerlines','110m',facecolor='none',edgecolor='tab:blue',lw=.2)); ax.add_feature(cfeature.NaturalEarthFeature('physical','lakes','50m',facecolor='tab:blue',edgecolor='tab:blue',lw=.2,alpha=.5))
    cont = ((tx_idxmaxtime>=pd.Timestamp(datetime.strptime(regmaptimes[regsel].start,"%B %d, %Y")))&(tx_idxmaxtime<=pd.Timestamp(datetime.strptime(regmaptimes[regsel].stop,"%B %d, %Y")))).where(lsm>.5).T.plot.contourf(ax=ax,colors='none',levels=[.5,1.5],hatches=['','/////////'],add_colorbar=False,transform=ccrs.PlateCarree()); [c.set_rasterized(True) for c in cont.collections]
    ax.set_title('')
    ax.set_title(panellabel,weight='bold',loc='left')
    ax.set_title(f'{datetime.strptime(time.start,"%B %d, %Y").strftime("%b. %-d")} – {datetime.strptime(time.stop,"%B %d, %Y").strftime("%b. %-d")}, {time.start[-4:]}',style='italic',loc='right')
    ax.plot([reglon[0],reglon[1],reglon[1],reglon[0],reglon[0]],[reglat[0],reglat[0],reglat[1],reglat[1],reglat[0]],color='0',lw=1.75,transform=ccrs.PlateCarree())
    ax.plot([reglon[0],reglon[1],reglon[1],reglon[0],reglon[0]],[reglat[0],reglat[0],reglat[1],reglat[1],reglat[0]],color='1',lw=.75,transform=ccrs.PlateCarree())
    ax.set_global()

reglist = [0,1,2,3]
qqs = [reg_tx_maxanoms[n] for n in reglist]
qq2s = [reg_tx_meananoms[n] for n in reglist]
dates = [reg_tx_maxanomdates[n] for n in reglist]
offsets = [0]*len(reglist)
titles = [regtitles[n] for n in regsels]
panellabels = [letter for letter in ascii_lowercase[1::2][:len(regsels)]]
axs_right = []
for gs,qq,qq2,date,offset,title,panellabel in zip(gs_right,qqs,qq2s,dates,offsets,titles,panellabels):
    ax = fig.add_subplot(gs); axs_right.append(ax)
    ax.grid(c='.9')
    qq.plot(ax=ax,lw=1,color='0',marker='o',markersize=2)
    eventyear,eventval = qq.idxmax('year').values,qq.max('year').values
    ax.plot(eventyear,eventval,marker='o',color='tab:red')
    ax.annotate(f"{date.sel(year=eventyear).dt.strftime('%b. %-d, %Y').values}",(eventyear,eventval),color='tab:red',ha='right',va='center',xytext=(-7,offset),textcoords='offset points') #, {int(eventyear)}
    ax.set_xlim(1949,2025)
    ax.set_xlabel('')
    ax.tick_params(axis='x',label1On=False)
    ax.set_ylabel('Tx anomaly [°C]')
    ax.set_title(panellabel,loc='left',weight='bold')
    ax.set_title(f'{title}',loc='right',style='italic')
    ax.tick_params(axis='x',label1On=True)

fig.canvas.draw()
fig.suptitle('Record-breaking heatwaves',x=axs_left[0].get_position().x0-.0025,y=1,ha='left',va='bottom',fontsize=12)
fig.text(axs_right[0].get_position().x0,1,'Summer-max. regional-mean Tx anomaly',ha='left',va='bottom',fontsize=12)


Text(0.5138274272214602, 1, 'Summer-max. regional-mean Tx anomaly')

<Figure size 17496x25920 with 12 Axes>